In [8]:
import numpy as np
import plotly.express as px

import os
from cmdstanpy import CmdStanModel, cmdstan_path

import git
git_root = git.Repo(search_parent_directories=True).git.rev_parse("--show-toplevel")

In [9]:
varying_file = os.path.join(git_root, 'src', 'models', 'stan', 'varying.stan')
varying_model = CmdStanModel(stan_file = varying_file)

16:51:10 - cmdstanpy - INFO - compiling stan file /home/jimmyclowes85/code/choc-ranking/src/models/stan/varying.stan to exe file /home/jimmyclowes85/code/choc-ranking/src/models/stan/varying
16:52:18 - cmdstanpy - INFO - compiled model executable: /home/jimmyclowes85/code/choc-ranking/src/models/stan/varying


In [10]:
from src.data.generative import SimGenerative
sim = SimGenerative(n_people=40,
                    n_chocs=15,
                    seed=321)
sim.draw()

In [11]:
varying_fit = varying_model.sample(data={'n_people': sim.n_people,
                                        'n_chocs': sim.n_chocs,
                                        'rankings': np.flip(sim.choc_rankings, axis=1).astype('int')},
                                    step_size=0.01)

16:52:19 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

16:53:57 - cmdstanpy - INFO - CmdStan done processing.


16:53:57 - cmdstanpy - WARNING - Some chains may have failed to converge.
	Chain 1 had 1 divergent transitions (0.1%)
	Chain 2 had 1 divergent transitions (0.1%)
	Chain 3 had 1 divergent transitions (0.1%)
	Use function "diagnose()" to see further information.


In [12]:
fig = px.violin(varying_fit.stan_variable('choc_mus_fitted'))
for i in range(0, sim.n_chocs):

    fig.add_shape(
        type='line',
        x0=(i-0.5),
        y0=(sim.choc_mus[i]),
        x1=i+0.5,
        y1=(sim.choc_mus[i]),
        line=dict(
            color='Red',
        )
    )


fig.update_layout(
{
'plot_bgcolor': 'rgba(0, 0, 0, 0)',
'paper_bgcolor': 'rgba(0, 0, 0, 0)'
},
showlegend=False)

fig.update_xaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='chocolate')
fig.update_yaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='underling preference')

fig.show()

In [13]:
fig = px.violin(varying_fit.stan_variable('choc_sigmas_fitted'))
for i in range(0, sim.n_chocs):

    fig.add_shape(
        type='line',
        x0=(i-0.5),
        y0=(sim.choc_sigmas[i]),
        x1=i+0.5,
        y1=(sim.choc_sigmas[i]),
        line=dict(
            color='Red',
        )
    )


fig.update_layout(
{
'plot_bgcolor': 'rgba(0, 0, 0, 0)',
'paper_bgcolor': 'rgba(0, 0, 0, 0)'
},
showlegend=False)

fig.update_xaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='chocolate')
fig.update_yaxes(showline=True,
                    linewidth=1,
                    linecolor='black',
                    title='variation in preferences')

fig.show()